# Calculate Urban Metrics: Sprawl
Normalized difference between the share of areas with population density below the regional average density and the share of areas with population density above the regional average density (Fallah et al., 2011).

Sprawl L H = ((L%−H%)+1)*0.5

Where L% is the share of metropolitan population living in a grid cell with density below the overall grid cell group median and H% is the share of metropolitan population living in a grid cell with density above the overall grid cell group median. The sprawl measure in Equation (8) is an index that ranges between 0 and 1; values closer to 1 represent greater sprawl.

To account for ‘rural clusters’ in metropolitan areas, grid cells with density below 200 persons per square mile are excluded (or 77 per square km).

In [37]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [38]:
import sys
import time

In [39]:
import pandas as pd
import geopandas as gpd
import numpy as np

In [40]:
from shapely.geometry import mapping
from shapely.geometry import Point

In [41]:
# Get reference to GOSTNets
sys.path.append(r"C:\repos\INFRA_SAP")
from infrasap.urban_metrics import *

In [42]:
import rasterio
from rasterio.mask import mask
from rasterio import Affine  # or from affine import Affine

In [43]:
start_time = time.time()

## Inputs are GHS pop and the urban extents
Mollweide projection should work good because it is an equal-area projection

In [44]:
GHS_pop = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\GHS_POP_E2015_GLOBE_R2019A_54009_1K_V1_0\GHS_POP_E2015_GLOBE_R2019A_54009_1K_V1_0.tif"
# GHS_pop = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\clipped_eca_no_russia_1km.tif"
# GHS_pop = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\2015_1km_GHS_Pop\GHS_POP_2015_UZB_merged.tif"

In [45]:
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\Final_urban_extent_metrics\ECA_all_urban_extents_100k_mollweide.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\russia_urban_extents_merged_mollweide.shp"
# shpName = r"C:\repos\GOST_Urban\Notebooks\Implementations\eca_wo_rus_urban_clusters_ghs_pop_smooth_100k_mollweide2.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_FUAs_Project_Mollweide.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_ghs_built_up_extents_4326\UZB_only_ghs_built_up_extents_mollweide_geom_fixed_greater_50k.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_ghs_built_up_extents_4326\UZB_ghs_built_up_extents_mollweide_geom_fixed.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\ECA_wo_rus_urban_extents\eca_wo_rus_built_up_extents_molleweide.shp"
shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\all_urban_clusters_5k_up_molleweide.shp"

## First find overall grid cell group median

In [46]:
# Psuedocode

# pop_values = []
# For each Shape/FUA:
# Select all built-up pixels that are mostly within shape (and exclude pixels less than 77 per square km)
# For each pixel:
# pop_values.append(pixel value)


# cell_group_median = median of pop_values

In [47]:
%%time

with rasterio.open(GHS_pop) as src:
    pixelSizeX, pixelSizeY = src.res
    print(pixelSizeX, pixelSizeY)

    input_shapes_gpd = gpd.read_file(shpName)

    # pop_values = []
    pop_values = []
    # for entry in input_shapes_gpd.head(2).iterrows():
    for entry in input_shapes_gpd.iterrows():
        print(entry[0])

        # extract the geometry in GeoJSON format
        geometry = entry[1]["geometry"]  # list of shapely geometries
        # geometry = geoms[0] # shapely geometry
        # converts to geojson format
        geoms = [mapping(geometry)]

        # extract the raster values values within the polygon
        out_image, out_transform = mask(src, geoms, crop=True, nodata=-9999.0)
        data = out_image[0, :, :]

        row, col = np.where(data != -9999.0)
        val = np.extract(data != -9999.0, data)

        # Adding the x,y, and geometry columns is not necessary
        T1 = out_transform * Affine.translation(0.5, 0.5)  # reference the pixel centre
        # row,column to x,y
        rc2xy = lambda r, c: (c, r) * T1

        d = gpd.GeoDataFrame({"col": col, "row": row, "val": val})

        # coordinate transformation
        d["x"] = d.apply(lambda row: rc2xy(row.row, row.col)[0], axis=1)
        d["y"] = d.apply(lambda row: rc2xy(row.row, row.col)[1], axis=1)

        # geometry
        d["geometry"] = d.apply(lambda row: Point(row["x"], row["y"]), axis=1)

        # exlude pixels with value less than 77
        print(len(d))

        # print(d)
        print(d.val[d.val > 77].to_list())

        print(len(d[d.val > 77]))

        # extend values to pop_values
        pop_values.extend(d.val[d.val > 77].to_list())

1000.0 1000.0
0
6
[426.4502258300781, 784.5906982421875, 1710.7764892578125, 867.53515625, 779.989990234375, 644.6363525390625]
6
1
9
[810.359375, 794.43896484375, 412.6275939941406, 553.48291015625, 1931.0897216796875, 374.7633056640625, 975.9127197265625, 1229.3065185546875, 1004.0221557617188]
9
2
10
[1665.9815673828125, 1745.388427734375, 1216.8602294921875, 303.71746826171875, 1572.401611328125, 2940.886962890625, 808.2916259765625, 585.3742065429688, 881.0283203125, 326.22723388671875]
10
3
8
[999.62109375, 1715.3323974609375, 1549.996826171875, 1189.90380859375, 1931.3685302734375, 2652.484130859375, 1270.6234130859375, 620.5514526367188]
8
4
56
[401.78326416015625, 423.4930725097656, 388.2616882324219, 329.97918701171875, 1025.0482177734375, 348.7073974609375, 1226.9041748046875, 1425.439697265625, 333.9139404296875, 534.088134765625, 384.62274169921875, 1092.7283935546875, 317.3013916015625, 4211.0185546875, 5073.52392578125, 2972.6162109375, 1336.884033203125, 2052.9653320312

C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\w


[457.7744445800781, 1311.59228515625, 1363.4659423828125, 631.123046875, 772.3285522460938, 2727.830810546875, 1195.49560546875]
7
17
11
[607.52880859375, 508.9964599609375, 394.8671875, 584.5299072265625, 417.61444091796875, 688.402587890625, 920.9430541992188, 1258.828369140625, 638.7916259765625, 936.6951293945312, 925.1766967773438]
11
18
16
[305.793212890625, 981.0064697265625, 728.6383056640625, 1369.959228515625, 1523.7489013671875, 331.2227783203125, 406.58453369140625, 416.3626403808594, 1919.793212890625, 2188.71044921875, 2306.544921875, 877.5816040039062, 1108.94873046875, 712.6543579101562, 1459.0333251953125, 348.0071105957031]
16
19
69
[764.9863891601562, 2891.039794921875, 910.1453857421875, 510.71441650390625, 1444.811767578125, 3466.873046875, 1879.5089111328125, 1337.67431640625, 1099.2164306640625, 1059.9993896484375, 4539.08447265625, 3876.80224609375, 1951.734375, 1375.064697265625, 575.9410400390625, 4521.39208984375, 4692.2939453125, 2835.983154296875, 2916.813

C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\w

57
[430.94805908203125, 605.0330810546875, 810.0535278320312, 1847.1082763671875, 776.6262817382812, 3408.95068359375, 2356.235595703125, 2059.15869140625, 1721.46240234375, 445.4737243652344, 877.7385864257812, 2553.35498046875, 727.8742065429688, 1316.448486328125, 4176.13623046875, 1716.8839111328125, 1597.6397705078125, 2063.352294921875, 313.44622802734375, 1096.6566162109375, 523.5087280273438, 622.4314575195312, 323.7205505371094, 1375.257568359375, 2390.432861328125, 315.51263427734375, 1069.671630859375, 1108.3651123046875, 1028.3402099609375, 495.4122009277344, 929.1405029296875, 1024.201904296875, 1213.647216796875, 1124.8321533203125, 862.5104370117188, 533.3743896484375, 1013.1896362304688, 830.68701171875, 766.28466796875, 1166.3624267578125, 750.3729858398438, 763.8807983398438, 372.43975830078125, 386.0813903808594, 453.61480712890625, 1235.4287109375, 516.8233642578125, 336.3591003417969, 2583.33837890625, 1044.10498046875, 2474.203369140625, 320.7231140136719, 591.295

...

6
[456.5051574707031, 803.470947265625, 1202.2703857421875, 392.2728271484375, 2449.260986328125, 433.9554748535156]
6
7951
6
[976.7506713867188, 793.8931884765625, 1155.4332275390625, 428.28643798828125, 2063.419921875, 1125.8333740234375]
6
7952
66
[725.3413696289062, 2876.590576171875, 1099.4322509765625, 727.256591796875, 1009.9298706054688, 2377.396240234375, 1638.7037353515625, 1254.5238037109375, 2400.880126953125, 1765.029052734375, 1138.8638916015625, 2507.60302734375, 1731.330810546875, 701.30810546875, 1960.5426025390625, 3617.648193359375, 3286.371337890625, 3008.946044921875, 3805.416259765625, 2108.984375, 2063.551025390625, 1352.4903564453125, 585.4573364257812, 381.7246398925781, 1512.5184326171875, 1477.777587890625, 1783.047119140625, 3152.16552734375, 898.8739013671875, 701.4962768554688, 1078.2198486328125, 2842.874267578125, 2786.382568359375, 1401.29541015625, 544.9797973632812, 1536.7154541015625, 1788.314453125, 1679.9847412109375, 595.3330078125, 2004.928833007

C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\w

203
[456.65179443359375, 491.010498046875, 566.1030883789062, 451.2615661621094, 768.7392578125, 912.1847534179688, 1568.583740234375, 342.29254150390625, 753.0587768554688, 1215.8515625, 3440.293701171875, 3181.142822265625, 1436.096923828125, 974.1486206054688, 777.2124633789062, 833.750732421875, 1153.7344970703125, 3878.025634765625, 3839.630615234375, 3707.893310546875, 1069.71533203125, 421.3822021484375, 1604.511474609375, 1741.314697265625, 1706.0220947265625, 1985.61376953125, 3678.10107421875, 3756.97021484375, 3594.22216796875, 2274.8525390625, 902.4893188476562, 1402.7552490234375, 1384.61669921875, 408.0938415527344, 380.37115478515625, 1797.173828125, 3349.442138671875, 2313.25244140625, 3002.349853515625, 2216.55419921875, 1048.8011474609375, 502.8033447265625, 2167.3818359375, 4138.67626953125, 2683.052734375, 3356.255615234375, 2829.335693359375, 3501.295654296875, 4533.95556640625, 4669.17431640625, 4224.33447265625, 4081.073974609375, 2755.78564453125, 2658.855224609

C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\war-machine\Anaconda2\envs\gostnets2\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Right multiplication will be prohibited in version 3.0
C:\Users\w

7
[348.8678283691406, 777.5620727539062, 1142.4613037109375, 461.3914489746094, 414.3523864746094, 1286.73974609375, 1477.8094482421875]
7
Wall time: 1min 9s


In [48]:
import statistics

UZB_pop_median = statistics.median(pop_values)

In [49]:
UZB_pop_median

1149.6275634765625

## Second calculate the Sprawl metric for each shape

In [50]:
# Psuedocode

# for each Shape/FUA:
# pixel_count_below_median = 0
# pixel_count_above_median = 0

# Select all built-up pixels that are mostly within shape (and exclude pixels less than 77 per square km)
# calculate pixel_share_below_median and pixel_share_above_median

# Sprawl = ((L%−H%)+1)*0.5
# Sprawl = ((pixel_share_below_median-pixel_share_above_median)+1)*.5

In [51]:
%%time

with rasterio.open(GHS_pop) as src:
    pixelSizeX, pixelSizeY = src.res
    print(pixelSizeX, pixelSizeY)

    input_shapes_gpd = gpd.read_file(shpName)

    # pixel_count_below_median = 0
    pixel_count_below_median = 0
    # pixel_count_above_median = 0
    pixel_count_above_median = 0

    # for entry in input_shapes_gpd.head(3).iterrows():
    for entry in input_shapes_gpd.iterrows():
        print(entry[0])

        # extract the geometry in GeoJSON format
        geometry = entry[1]["geometry"]  # list of shapely geometries
        # geometry = geoms[0] # shapely geometry
        geoms = [mapping(geometry)]

        # extract the raster values values within the polygon
        out_image, out_transform = mask(src, geoms, crop=True, nodata=-9999.0)
        data = out_image[0, :, :]

        row, col = np.where(data != -9999.0)
        val = np.extract(data != -9999.0, data)

        d = gpd.GeoDataFrame({"col": col, "row": row, "val": val})

        # exlude pixels with value less than 77
        d = d[d.val > 77]
        d_count = len(d)
        # print(f"d_count is {d_count}")

        # print(d.val[d.val < UZB_pop_median])
        # print(len(d.val[d.val < UZB_pop_median]))
        pixel_share_below_median = len(d.val[d.val < UZB_pop_median]) / d_count
        print(f"pixel_share_below_median is: {pixel_share_below_median}")

        # print(d.val[d.val > UZB_pop_median])
        # print(len(d.val[d.val > UZB_pop_median]))
        pixel_share_above_median = len(d.val[d.val > UZB_pop_median]) / d_count
        print(f"pixel_share_above_median is: {pixel_share_above_median}")

        # Sprawl = ((L%−H%)+1)*0.5
        # Sprawl = ((pixel_count_below_median-pixel_count_above_median)+1)*.5
        Sprawl = ((pixel_share_below_median - pixel_share_above_median) + 1) * 0.5
        print(f"Sprawl index is: {Sprawl}")

        # creates a temporary GDF for just the row's shape
        temp_gdf = input_shapes_gpd.iloc[[entry[0]]]

        # print("print temp_gdf")
        # print(temp_gdf)

        # Put all metrics in a DataFrame
        metrics_scalar = {}
        metrics_scalar["sprawl_index"] = [Sprawl]
        metrics_df = pd.DataFrame(metrics_scalar)

        # print("print metrics_scalar")
        # print(metrics_scalar)

        # and concatinate it with the row's shape
        new_temp_gdf = pd.concat([temp_gdf.reset_index(drop=True), metrics_df], axis=1)

        # print("print new_temp_gdf")
        # print(new_temp_gdf)
        # print(entry[0])
        # put the results of each row into a new DataFrame
        if entry[0] == 0:
            print("new_temp_gdf")
            output_new_temp_gdf = new_temp_gdf
        else:
            output_new_temp_gdf = output_new_temp_gdf.append(
                new_temp_gdf, ignore_index=True
            )

1000.0 1000.0
0
pixel_share_below_median is: 0.8333333333333334
pixel_share_above_median is: 0.16666666666666666
Sprawl index is: 0.8333333333333334
new_temp_gdf
1
pixel_share_below_median is: 0.7777777777777778
pixel_share_above_median is: 0.2222222222222222
Sprawl index is: 0.7777777777777778
2
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
3
pixel_share_below_median is: 0.25
pixel_share_above_median is: 0.75
Sprawl index is: 0.25
4
pixel_share_below_median is: 0.4642857142857143
pixel_share_above_median is: 0.5357142857142857
Sprawl index is: 0.4642857142857143
5
pixel_share_below_median is: 0.4782608695652174
pixel_share_above_median is: 0.5217391304347826
Sprawl index is: 0.4782608695652174
6
pixel_share_below_median is: 0.7272727272727273
pixel_share_above_median is: 0.2727272727272727
Sprawl index is: 0.7272727272727273
7
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.6666

78
pixel_share_below_median is: 0.6
pixel_share_above_median is: 0.4
Sprawl index is: 0.6
79
pixel_share_below_median is: 0.36363636363636365
pixel_share_above_median is: 0.6363636363636364
Sprawl index is: 0.36363636363636365
80
pixel_share_below_median is: 1.0
pixel_share_above_median is: 0.0
Sprawl index is: 1.0
81
pixel_share_below_median is: 0.5555555555555556
pixel_share_above_median is: 0.4444444444444444
Sprawl index is: 0.5555555555555556
82
pixel_share_below_median is: 0.4375
pixel_share_above_median is: 0.5625
Sprawl index is: 0.4375
83
pixel_share_below_median is: 0.4444444444444444
pixel_share_above_median is: 0.5555555555555556
Sprawl index is: 0.4444444444444444
84
pixel_share_below_median is: 1.0
pixel_share_above_median is: 0.0
Sprawl index is: 1.0
85
pixel_share_below_median is: 0.75
pixel_share_above_median is: 0.25
Sprawl index is: 0.75
86
pixel_share_below_median is: 0.5333333333333333
pixel_share_above_median is: 0.4666666666666667
Sprawl index is: 0.5333333333333

154
pixel_share_below_median is: 0.5217391304347826
pixel_share_above_median is: 0.4782608695652174
Sprawl index is: 0.5217391304347826
155
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
156
pixel_share_below_median is: 0.4
pixel_share_above_median is: 0.6
Sprawl index is: 0.4
157
pixel_share_below_median is: 0.625
pixel_share_above_median is: 0.375
Sprawl index is: 0.625
158
pixel_share_below_median is: 0.625
pixel_share_above_median is: 0.375
Sprawl index is: 0.625
159
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.6666666666666666
160
pixel_share_below_median is: 0.7777777777777778
pixel_share_above_median is: 0.2222222222222222
Sprawl index is: 0.7777777777777778
161
pixel_share_below_median is: 0.7
pixel_share_above_median is: 0.3
Sprawl index is: 0.7
162
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.666666

233
pixel_share_below_median is: 1.0
pixel_share_above_median is: 0.0
Sprawl index is: 1.0
234
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
235
pixel_share_below_median is: 0.5294117647058824
pixel_share_above_median is: 0.47058823529411764
Sprawl index is: 0.5294117647058824
236
pixel_share_below_median is: 0.75
pixel_share_above_median is: 0.25
Sprawl index is: 0.75
237
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.6666666666666666
238
pixel_share_below_median is: 0.5384615384615384
pixel_share_above_median is: 0.46153846153846156
Sprawl index is: 0.5384615384615384
239
pixel_share_below_median is: 0.6
pixel_share_above_median is: 0.4
Sprawl index is: 0.6
240
pixel_share_below_median is: 0.7142857142857143
pixel_share_above_median is: 0.2857142857142857
Sprawl index is: 0.7142857142857143
241
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333

309
pixel_share_below_median is: 1.0
pixel_share_above_median is: 0.0
Sprawl index is: 1.0
310
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
311
pixel_share_below_median is: 0.49295774647887325
pixel_share_above_median is: 0.5070422535211268
Sprawl index is: 0.49295774647887325
312
pixel_share_below_median is: 0.875
pixel_share_above_median is: 0.125
Sprawl index is: 0.875
313
pixel_share_below_median is: 0.9090909090909091
pixel_share_above_median is: 0.09090909090909091
Sprawl index is: 0.9090909090909091
314
pixel_share_below_median is: 0.38461538461538464
pixel_share_above_median is: 0.6153846153846154
Sprawl index is: 0.3846153846153846
315
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.6666666666666666
316
pixel_share_below_median is: 0.6842105263157895
pixel_share_above_median is: 0.3157894736842105
Sprawl index is: 0.6842105263157895
317
pixel_share_below_median is: 0.71

...

pixel_share_below_median is: 0.6
pixel_share_above_median is: 0.4
Sprawl index is: 0.6
7689
pixel_share_below_median is: 0.5263157894736842
pixel_share_above_median is: 0.47368421052631576
Sprawl index is: 0.5263157894736842
7690
pixel_share_below_median is: 0.8333333333333334
pixel_share_above_median is: 0.16666666666666666
Sprawl index is: 0.8333333333333334
7691
pixel_share_below_median is: 0.625
pixel_share_above_median is: 0.375
Sprawl index is: 0.625
7692
pixel_share_below_median is: 0.625
pixel_share_above_median is: 0.375
Sprawl index is: 0.625
7693
pixel_share_below_median is: 0.7777777777777778
pixel_share_above_median is: 0.2222222222222222
Sprawl index is: 0.7777777777777778
7694
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
7695
pixel_share_below_median is: 0.5555555555555556
pixel_share_above_median is: 0.4444444444444444
Sprawl index is: 0.5555555555555556
7696
pixel_share_below_median is: 0.2674897119341564
pixel_share_above_medi

7781
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
7782
pixel_share_below_median is: 0.7
pixel_share_above_median is: 0.3
Sprawl index is: 0.7
7783
pixel_share_below_median is: 0.3333333333333333
pixel_share_above_median is: 0.6666666666666666
Sprawl index is: 0.33333333333333337
7784
pixel_share_below_median is: 0.875
pixel_share_above_median is: 0.125
Sprawl index is: 0.875
7785
pixel_share_below_median is: 0.5666666666666667
pixel_share_above_median is: 0.43333333333333335
Sprawl index is: 0.5666666666666667
7786
pixel_share_below_median is: 0.5384615384615384
pixel_share_above_median is: 0.46153846153846156
Sprawl index is: 0.5384615384615384
7787
pixel_share_below_median is: 0.8571428571428571
pixel_share_above_median is: 0.14285714285714285
Sprawl index is: 0.8571428571428571
7788
pixel_share_below_median is: 0.7333333333333333
pixel_share_above_median is: 0.26666666666666666
Sprawl index is: 0.7333333333333333
7789
pixel_share_below_media

pixel_share_below_median is: 0.3783783783783784
pixel_share_above_median is: 0.6216216216216216
Sprawl index is: 0.3783783783783784
7852
pixel_share_below_median is: 0.36363636363636365
pixel_share_above_median is: 0.6363636363636364
Sprawl index is: 0.36363636363636365
7853
pixel_share_below_median is: 0.7272727272727273
pixel_share_above_median is: 0.2727272727272727
Sprawl index is: 0.7272727272727273
7854
pixel_share_below_median is: 0.4
pixel_share_above_median is: 0.6
Sprawl index is: 0.4
7855
pixel_share_below_median is: 0.5714285714285714
pixel_share_above_median is: 0.42857142857142855
Sprawl index is: 0.5714285714285714
7856
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
7857
pixel_share_below_median is: 0.39705882352941174
pixel_share_above_median is: 0.6029411764705882
Sprawl index is: 0.3970588235294118
7858
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.666666666666

7921
pixel_share_below_median is: 1.0
pixel_share_above_median is: 0.0
Sprawl index is: 1.0
7922
pixel_share_below_median is: 0.7
pixel_share_above_median is: 0.3
Sprawl index is: 0.7
7923
pixel_share_below_median is: 0.3333333333333333
pixel_share_above_median is: 0.6666666666666666
Sprawl index is: 0.33333333333333337
7924
pixel_share_below_median is: 0.7142857142857143
pixel_share_above_median is: 0.2857142857142857
Sprawl index is: 0.7142857142857143
7925
pixel_share_below_median is: 0.4
pixel_share_above_median is: 0.6
Sprawl index is: 0.4
7926
pixel_share_below_median is: 0.6666666666666666
pixel_share_above_median is: 0.3333333333333333
Sprawl index is: 0.6666666666666666
7927
pixel_share_below_median is: 0.6
pixel_share_above_median is: 0.4
Sprawl index is: 0.6
7928
pixel_share_below_median is: 0.4
pixel_share_above_median is: 0.6
Sprawl index is: 0.4
7929
pixel_share_below_median is: 0.8571428571428571
pixel_share_above_median is: 0.14285714285714285
Sprawl index is: 0.8571428

7990
pixel_share_below_median is: 0.25
pixel_share_above_median is: 0.75
Sprawl index is: 0.25
7991
pixel_share_below_median is: 0.5
pixel_share_above_median is: 0.5
Sprawl index is: 0.5
7992
pixel_share_below_median is: 0.4
pixel_share_above_median is: 0.6
Sprawl index is: 0.4
7993
pixel_share_below_median is: 0.9
pixel_share_above_median is: 0.1
Sprawl index is: 0.9
7994
pixel_share_below_median is: 0.3333333333333333
pixel_share_above_median is: 0.6666666666666666
Sprawl index is: 0.33333333333333337
7995
pixel_share_below_median is: 0.7777777777777778
pixel_share_above_median is: 0.2222222222222222
Sprawl index is: 0.7777777777777778
7996
pixel_share_below_median is: 0.3333333333333333
pixel_share_above_median is: 0.6666666666666666
Sprawl index is: 0.33333333333333337
7997
pixel_share_below_median is: 0.7142857142857143
pixel_share_above_median is: 0.2857142857142857
Sprawl index is: 0.7142857142857143
Wall time: 1min 5s


In [52]:
output_new_temp_gdf

ID            Pop                             layer  \
0     2038    5213.978912                              None   
1     2355    8086.003265                              None   
2     2691   12046.157654                              None   
3     2753   11929.881653                              None   
4     3060  115285.056396                              None   
...    ...            ...                               ...   
7993    32    6807.330750  27_urban_clusters_ghs_pop_russia   
7994    28   20279.139618  27_urban_clusters_ghs_pop_russia   
7995    18    8344.212311  27_urban_clusters_ghs_pop_russia   
7996    15    5386.852844  27_urban_clusters_ghs_pop_russia   
7997    55    5909.184235  26_urban_clusters_ghs_pop_russia   

                                                   path  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
7993  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7994  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7995  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7996  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7997  C:/repos/GOST_Urban/Notebooks/Implementations/...   

                                               geometry  sprawl_index  
0     POLYGON ((2007000.000 6478000.000, 2010000.000...      0.833333  
1     POLYGON ((1952000.000 6468000.000, 1953000.000...      0.777778  
2     POLYGON ((1893000.000 6452000.000, 1897000.000...      0.500000  
3     POLYGON ((1934000.000 6450000.000, 1937000.000...      0.250000  
4     POLYGON ((2010000.000 6444000.000, 2011000.000...      0.464286  
...                                                 ...           ...  
7993  POLYGON ((7462000.000 6368000.000, 7466000.000...      0.900000  
7994  POLYGON ((7657000.000 6452000.000, 7660000.000...      0.333333  
7995  POLYGON ((7461000.000 6506000.000, 7462000.000...      0.777778  
7996  POLYGON ((8040000.000 6520000.000, 8041000.000...      0.333333  
7997  POLYGON ((8090000.000 7059000.000, 8091000.000...      0.714286  

[7998 rows x 6 columns]

In [54]:
# make the GeoDataFrame unprojected
output_new_temp_gdf = output_new_temp_gdf.to_crs("epsg:4326")

# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_metrics_results_russia"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_urban_metrics_results_wo_rus"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_FUAs_results"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_urban_extents_results"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_urban_extents_results_all"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_urban_metrics_results_wo_rus_all"
output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\all_urban_extents_results_5k_up"

# save as CSV

# output_new_temp_gdf.to_csv(output + r"\ECA_all_urban_metrics_100k_sprawl.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_FUAs_sprawl.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_urban_extents_sprawl.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_urban_extents_all_sprawl.csv")
# output_new_temp_gdf.to_csv(output + r"\ECA_wo_rus_urban_metrics_urban_extents_all_sprawl.csv")
output_new_temp_gdf.to_csv(output + r"\all_urban_metrics_5k_up_sprawl.csv")

In [ ]:
print(f"total time to process: {time.time()-start_time}")